Lecture notes for the course
# Computer-Guided Data Analysis
in the Bachelor's study program in Physics at Karlsruhe Institute of Technology (KIT)

U. Husemann (based on material from G. Quast, T. Ferber and U. Husemann)

Summer Semester 2024

# Chapter 3: Digital Signal Processing

## Digital data

<a name="measure"></a>
### What is measurement?
To understand the relevance of digital data in modern physics, it is worth taking an abstract look at the process of measurement. To have a concrete example in mind, you can always imagine measurement as the determination of an electrical resistance by means of a current-voltage characteristic.

In a measurement, an input variable is measured, e.g., a length or time interval, a current or a voltage. The aim of the measurement is to obtain a physically meaningful result and its uncertainty. To obtain this, a few intermediate steps are usually necessary:
1. The measurement takes place with a measuring device or a **sensor**. As a physicist, your task is not to view the sensor as a "black box", but to understand exactly how it works. For example, it may be necessary to calibrate the sensor.
1. It may be advantageous to repeat the measurement **several times**. In this course you have already learned how this can reduce the measurement uncertainty.
1. The **measurement signal** is then the response of the measuring device to an input. Most modern measuring devices are electronic, and the measurement signal is therefore often an analog electrical signal, either a current or a voltage.  
1 Today, most measurement signals are processed further using a computer. To do this, the analog electrical signal must be converted into a **digital signal**. At this point, corrections are often made to the data, e.g., to perform the above-mentioned calibration.
1. The digital signal is then either processed further in real time or temporarily stored before further processing. Intermediate storage takes place in **digital file formats**, which you will become familiar with in this chapter.
1. The digital signal is analyzed on the computer, often using statistical data analysis methods. The final measured quantity and its uncertainty result from the comparison of the digital signal with a physics model (e.g. Ohm's law for the relationship between current and voltage for an electrical resistance). This is the subject of chapter 4.

### Digital sampling and quantization
Analog signals are **continuous**, both as a function of time and as a function of signal value. To convert an analog signal into a digital signal, it must be **discretized** both in time and in signal value (see code example):
- Digital **sampling** is used to determine the signal value at certain fixed points in time. This is often done with a fixed clock rate.
- **Quantization** is used to map the analog signal value to an integer with $m$ bits. This results in $2^m - 1$ possible digital signal values.

In [ ]:
"""illustration of sampling and quantization of an analog signal"""
import numpy as np
import matplotlib.pyplot as plt

fig, ax =  plt.subplots( 2, 2, figsize=(12,8) )
tmin, tmax = -0.5, 6.5 

# analog signal is a sine wave
t = np.linspace( 0, 2*np.pi, 200 )
wave = np.sin(t)
ax[0][0].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[0][0].plot( t, wave, label="Analog Signal" )
ax[0][0].set_xlabel( "$t$" )
ax[0][0].set_ylabel( "Continuous Signal Value" )
ax[0][0].set_xlim( tmin, tmax )
ax[0][0].legend()

# time discrete signal
n = np.linspace( 0, 6, 12 )
sample = np.sin(n)
ax[0][1].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[0][1].stem( n, sample, label="Time Discrete Signal" )
ax[0][1].set_xlabel( "$n$" )
ax[0][1].set_ylabel( "Continuous Signal Value" )
ax[0][1].set_xlim( tmin, tmax )
ax[0][1].legend()

# analog signal quantized
step=0.2
quant = step*np.round( np.sin(t)/step )
ax[1][0].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[1][0].stairs( quant[:-1], edges=t, label="Quantized Signal" )
ax[1][0].set_xlabel( "$t$" )
ax[1][0].set_ylabel( "Discrete Signal Value" )
ax[1][0].set_xlim( tmin, tmax )
ax[1][0].legend()

# time discrete signal quantized
discrete_quant = step*np.round( sample/step )
ax[1][1].hlines( 0, tmin, tmax, linestyle="dashed" )
ax[1][1].stem( n, discrete_quant, label="Time Discrete Quantized Signal" )
ax[1][1].set_xlabel( "$n$" )
ax[1][1].set_ylabel( "Discrete Signal Value" )
ax[1][1].set_xlim( tmin, tmax )
ax[1][1].legend()

plt.show()

#### Analog-to-digital converters
Devices for sampling and quantizing analog signals are referred to as analog-to-digital converters (ADCs). Important key figures for ADCs are the sampling frequency and the resolution in bits. In the following code example, a sinusoidal signal is digitized with a 4-bit ADC and ten samples per period.

In [ ]:
# illustrate principle of signal sampling
# UH after G. Quast's example code

import numpy as np, matplotlib.pyplot as plt
from  scipy import interpolate

mnx = 0.
mxx = 1.5*np.pi
nbins = 7
xplt = np.linspace(mnx, mxx, nbins+1) # range in x
nplt = nbins * (xplt-mnx)/(mxx-mnx)   # sample number - 1

xana = np.linspace( mnx, mxx, 200 )   # analog values
nana = nbins * (xana-mnx)/(mxx-mnx)
yana = np.sin( xana )

yplt = np.sin(xplt)

miny = min(yplt)
maxy = max(yplt)

# quantization
nbits = 4
step  = ( maxy - miny ) / 2**nbits
quant = step * np.round( yplt/step )

fig,ax = plt.subplots( figsize=(6,5) )
minyp = miny - 0.05*( maxy - miny )
maxyp = maxy + 0.05*( maxy - miny )
ax.set_xlim( 0., nbins+2 )
ax.set_ylim( minyp, maxyp )

# plot sampled curve
ax.plot( nana+1, yana, 'r--', label='Analog Signal')

# plot individual measurements as markers
ax.plot( nplt+1, quant, 'o', color='steelblue', label='Measurements (%d bits)' % nbits ) 

# indicate sampling points as vert. lines
ax.vlines( nplt+1, minyp, yplt, colors='steelblue', linestyles='--' )
    
# axis labels and legend
ax.set_xlabel( r'Sampling, $n = t \,\nu_s$', size='large' )
ax.set_ylabel( 'Value', size='large' )
ax.legend( numpoints=1, loc='best', prop={'size':12} )

plt.show()


In the example above, the ADC provides a new value each time it is sampled. However, it is also possible to read out signals more frequently. This technique is known as **oversampling**. It can be shown that oversampling suppresses (uncorrelated) noise better than the signal and hence improves the signal-to-noise ratio (SNR). To see the effect, try the above code with more sample points (`nbins=20`) and lower resolution (`nbits=3`).

>**Note: WKS sampling theorem** 
>
>The "appropriate" sampling frequency for a signal with a bandwidth (difference between highest and lowest frequency) of $\nu_\mathsf{max}$ results from the Whittaker-Kotelnikov-Shannon (WKS) sampling theorem, also called Nyquist-Shannon sampling theorem in older literature. The WKS theorem states that a signal of bandwidth $\nu_\mathsf{max}$ can be reconstructed exactly from equidistant samples if it is sampled with a frequency of at least $2\nu_\mathsf{max}$. In this context, an $n$-fold oversampling is a sampling with $2n\nu_\mathsf{max}$.

<a name="interpolation"></a>
### Interpolation
As can be seen from the figures above, the best way of displaying digital data is to show individual data points - the data is only available for these fixed points in time and with the resolution of the ADC. However, it can happen that intermediate values are required or an **interpolation** of the data points is useful as a graphical aid ("to guide the eye"). This is "permitted" insofar as analog signals almost always behave "smoothly" between two samples (i.e. we expect their function graphs to be continuous or even continuously differentiable).

Matplotlib displays a continuous connection of the discrete points by adding the following lines (before the `plt.show()`) to the above code:
```
# connect points by straight line
ax.plot( nplt+1, quant, 'b--', label = 'Linear Interpolation' )
```
An interpolation with **cubic splines**, i.e. continuously differentiable curves from third degree polynomial pieces, as introduced in the course "Programming and Algorithms" in chapter 9, can be obtained with the following code:
```
# cubic spline interpolation
cs_y = interpolate.UnivariateSpline( nplt, quant, s=0 )
xplt2 = np.linspace( -0.5, nbins+0.5, 200 )
ax.plot(xplt2+1, cs_y(xplt2), 'g-.', lw=2, label = 'Spline Interpolation')
```

## Digital data formats

### Data and its meaning
In order to learn something from data, it is important to know what the data **means**. Very rarely, data is self-explanatory; additional information is almost always required to define the data set. This is known as **metadata**.

**Example**: You have recorded the following pairs of values with the computer in the laboratory course:
```[5.26389273 4.11237443]
[5.64990981 6.31579031]
[3.31035396 2.72230292]
[5.11071304 4.74767761]
[4.98544977 4.13855549]
[5.76158099 6.21749092]
[5.05718426 6.16025656]
[5.40487497 4.37446221]
...
```
You will only be able to assign a meaning to the pairs of values if you have also noted which variables were measured and in which units. For example, the first column could represent electrical voltages in volts that you dialed into a power supply and the second the current you measured at this voltage in milliamperes. This metadata is therefore required in addition to the data in order to be able to interpret the data.

>**Note**: The **Rosetta Stone** is a historical example of the meaning of data. The Rosetta Stone dates back to Hellenistic times and was rediscovered in Egypt in 1799. The stone was central to the translation of ancient Egyptian hieroglyphics, the meaning of which was unknown in early 19th century Europe. It helped that the same text was inscribed on the stone in three different languages and scripts, including the already well-known ancient Greek. In this example, it was only possible to learn something from the data in the hieroglyphs once their meaning had been clarified.

>**Excursus: Handling research data** 
>
>Trust in science and its results is achieved, among other things, by the fact that scientific results must (at least in principle) be comprehensible to other people at all times. The [German Research Foundation](https://www.dfg.de) (DFG), the most important public funding body for research in Germany, has drawn up rules to this end that require
>- **Reuse and further use** of research data must be made possible.
>- Research data must be suitably archived for **at least ten years**.
>
> These rules naturally also apply internationally. When storing research data, the **FAIR principles** must be fulfilled:
>- **Findable**: Data should be retrievable.
>- **Accessible**: Data should be accessible in the long term.
>- **Interoperable**: Data should be technically reusable and combinable with other data sets.
>- **Reusable**: Data should be analytically and intellectually reusable.

### Overview of digital data formats
You have already learned about some common digital data formats in the course "Programming and Algorithms" (Lecture 12 in the winter semester 2023/2024). In this course, this discussion will be taken up again. Digital file formats can be divided into binary and text files:
- **Binary files** are only machine-readable and their encoding is often system-dependent. Examples include compiled computer programs, image and audio files and compressed file formats.
- **Text files** can be read by both machines and humans; however, there are different character encoding standards.

>Common standards for **character encoding** in text files:
>- **ASCII** (American Standard Code for Information Interchange) uses a 7-bit encoding. This results in 128 characters, 95 of which are printable, the remaining 33 characters are control characters (e.g. line feed, tabulator).
>- **ISO 8859-x**: This ISO standard combines various extensions of the ASCII coding to 8 bits in order to be able to display additional characters. For example, the ISO 8859-1 "Western" encoding contains special characters for many Latin alphabets of the Western world, including German umlauts. There are also variants of this standard, e.g. the standard Windows-1252 (also: ANSI) especially for Microsoft Windows.
>- **UTF-8** (Universal Coded Character Set Transformation Format, or Unicode for short): this encoding standard can be used to display characters for all languages worldwide with byte strings of variable length (up to four bytes). UTF-8 is currently (2024) the de facto standard for character encoding on the Internet.

#### Example: CSV
**CSV** (comma-separated values) is a very common format for tabulated data. The data is available as a human-readable text file and usually has one or more header lines with metadata. The cell phone app [phyphox](https://phyphox.org), for example, provides the following data when the three accelerometers of the cell phone are read out:
```
"Time (s)", "X (m/s^2)", "Y (m/s^2)", "Z (m/s^2)"
0.000000000E0,1.621128845E-1,-1.346450043E0,1.007988876E1
1.002300000E-2,1.779798889E-1,-1.441951447E0,1.033151550E1
2.004599999E-2,2.393522644E-1,-1.292412415E0,1.030891251E1
3.006900000E-2,2.058219910E-1,-1.199306030E0,1.024020538E1
...
```
The header line provides the metadata in the form of the size and unit for each column. The columns are separated by a delimiter. In addition to the eponymous comma, this could also be a semicolon, space, tab or similar. The format is therefore particularly suitable for tables, i.e. "flat" two-dimensional data consisting of rows and columns. Simple measuring devices in physics laboratory courses, cell phone apps such as phyphox or data loggers often use the CSV format. Here, the data consists of floating point numbers, as in the example above.

CSV files can be read and saved in spreadsheet programs (Microsoft Excel, LibreOffice Calc, Apple Numbers, ...), for example. There are also several ways to read and write CSV files in Python, e.g., with `np.genfromtxt`, they can be loaded directly into NumPy arrays:

In [ ]:
# reading a CSV file is a one-liner in NumPy, using np.genfromtext
# arguments: file name, delimiter, number of header lines to be skipped
import numpy as np
data = np.genfromtxt( "data/Accelerometer.csv", 
                      delimiter=",", 
                      skip_header=1 )

# print first five lines of file
print( data[0:5] )

Further variants of working with CSV files can be found in lecture 12 of the course "Programming and Algorithms", e.g. with the Python module `csv` or in pandas. The software tool for the physics laboratory course presented in chapter 4 [`PhyPraKit`](ekpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/) also contains corresponding functions. These are particularly useful if the measuring devices in the physics laboratory course output internationally unusual data formats, e.g, with a decimal comma instead of a decimal point.

#### Self-describing file formats
In physics, data structures often go far beyond what can be meaningfully represented with two-dimensional tables of floating point numbers. For example, the collisions of elementary particles recorded in the experiments at the Large Hadron Collider (LHC) at CERN provide data sets with a rich hierarchical structure. This includes the reconstructed properties of all particles produced in a collision and their decay products.

Such data structures cannot be meaningfully realized with CSV files. In particle physics, specially developed binary file formats are used. The following discussion with concentrate on self-describing human-readable (text) file formats that are also used in physics, e.g. as configuration files for programs.
These files have a format that uses specific **tags** to describe the data structure within the file. There are several common **markup languages** that contain such tags.

>**Excursus: Markup languages** 
>
>Markup languages label data using markers, called **tags**. Examples include:
>- **HTML** (Hypertext Markup Language) is the basic language for websites. For example, in HTML, a heading of the first hierarchy level is marked with the following tag: `<h1>Heading 1</h1>`.
>- **$\LaTeX$** is the standard language for typesetting scientific texts. A section heading in $\LaTeX$ looks like this: `\section{section heading}`.
>- **Markdown**, the language for text passages in Jupyter notebooks, in which this script is also written, has simplified tags compared to other markup languages. A heading of the first hierarchy level is marked in Markdown with: `# Heading 1`.
>
> These examples are in contrast to the **WYSIWYG approach** ("what you see is what you get"), which is still possible in word processing programs such as Microsoft Word, Apple Pages or LibreOffice Writer: for a heading, a text is simply typeset in larger bold letter. In most cases, it is better to **separate the form and content** of documents. To do this, users enter the heading as text and also specify: "This text is a heading". The program then provides a suitable typesetting. This is possible both in markup languages (using tags) and in modern word processing programs.

Examples of common self-describing data formats that are well supported in Python and are also frequently used on the Internet include the following formats:
- **XML** (Extensible Markup Language) forms the basis for HTML and allows you to define your own self-describing file formats with your own tags, e.g.
```
      <Data>
            <Time>
                  <Value>1.002300000E-2</Value>
                  <Unit>s</Unit>
            </Time>
            <Accelerometer>
                  <Value Coord="x">1.7797988E-1</Value>
                  <Value Coord="y">-1.4419514E0</Value>
                  <Value Coord="z">1.0331515E1</Value>
                  <Unit>m/s^2</Unit>
            </Accelerometer>
            <Gyroscope>
                  ...
            </gyroscope>
      </data>
```
- **JSON** (JavaScript Object Notation, pronunciation: Jason) is the format in which Jupyter notebooks, among others, are saved - take a look at this document with a text editor, for example. Python dictionaries also use this format. The above example in XML looks like this in JSON:
```
      {
            "Name" : Data,
            "Time" : 1.002300000E-2,
            "Unit Time" : "s",
            "Accelerometer" :
            {
                  "x Value" : 1.7797988E-1,
                  "y Value" : -1.4419514E0,
                  "z Value" : 1.0331515E1,
                  "Unit" : "m/s^2"
            },
            "Gyroscope" :
            {
                  ...
            },
      }
```
- **YAML** (YAML Ain't Markup Language) is a somewhat more compact format that is used, for example, to configure software, including the analysis tool [`PhyPraKit`](https://etpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/) in the physics laboratory course, which will be introduced in chapter 4. The underlying fitting framework [`kafe2`](https://kafe2.readthedocs.io/en/latest/index.html#) offers the a command line interfaces (`kafe2go`) using YAML configuration files as well. The recursive acronym of the name YAML reflects the humor of the scene in which the format was created. The above example has the following form in YAML:
```
      --- # Data
      Time: 0.010023
      Unit Time: s
      Accelerometer:
            x Value: 1.7797988E-1
            y Value: -1.4419514E0
            z Value: 1.0331515E1
            Unit: m/s^2
      Gyroscope:
            ...
      ```

## Digital signal processing
The raw electrical signals from sensors are usually [processed](#measured) over several stages before they are finally evaluated on the computer. Even the analog current or voltage signals can be suitably shaped using specialized analog electronics before digitization (signal shaping). Due to the greater flexibility of computer code compared to sepecialized electronics and the high performance of modern computers, an increasing proportion of signal processing is shifting to the post-digitization stage. Techniques of **digital signal processing** (DSP) include, among others:
- **Interpolation** between known data points (see above).
- **Frequency analysis**: Transformation of time series into frequency spectra using Fourier transform (and vice versa using inverse Fourier transform).
- **Digital filtering** in position space, time domain or frequency domain.
- **Correlation analysis**: Cross-correlation and autocorrelation.

The **interpolation** of digital data, i.e., the approximation of unknown values between known data points, has already been covered in the course "Programming and Algorithms" (Chapter 9). Code examples for linear interpolation and interpolation with cubic splines can be found earlier in this chapter, in the section on [Sampling and quantization](#interpolation).

### Frequency analysis
Time-dependent physical phenomena, such as oscillations and waves, can be represented in the **time domain** or, equivalently, in the **frequency domain**.  Mathematically, these phenomena can be represented as functions $f(t)$, which are expanded in a Fourier series as a function of the angular frequency $\omega$:
$$
f(t) = \frac{a_0}{2} + \sum_{m=1}^\infty
\big[
c_m \cdot \cos( m\cdot \omega t ) +
b_m \cdot \sin( m\cdot \omega t )
\big].
$$
In this equation, $a_n$ and $b_n$ are the Fourier coefficients for the frequency $\nu_m = m\omega/(2\pi)$. The signal level in frequency space is then $c_m \equiv \sqrt{c_m^2 + b_m^2}$. Equivalently, the Fourier series can also be written with complex coefficients $c_m$:
$$
f(t) = \sum_{m=0}^\infty
c_m \exp\left[ i\,m\cdot\omega t\right].
$$

Digital signals in the time domain consist of a series of time-ordered discrete data points. This series is referred to as a **time series**. For such time series, there is a numerically very efficient method for Fourier transformation, which is called **fast Fourier transform** (FFT). Carl Friedrich Gauss had the first ideas for this method at the beginning of the 19th century, but since the 1960s the FFT has been widely available with the algorithm of James William Cooley and John Wilder Tukey and is generally regarded as **one of the most important computer algorithms of all**. Both NumPy and SciPy have easy-to-use FFT modules (`numpy.fft` and `scipy.fft`).

In the following code example, a human voice was recorded with the cell phone app [phyphox](phyphox.org) and saved as a time series in CSV format. The CSV file is read in and transformed into frequency space using the FFT module of NumPy.

In [ ]:
"""FFT: fast Fourier transform"""
import numpy as np
import matplotlib.pyplot as plt
from scipy import signal

# read audio signal
data = np.genfromtxt('data/phyphox_voice.csv', delimiter=",", skip_header=1 )
t = data[:,0]    
x = data[:,1]
N = len(x) 
sampling = 48000 # match Phyphox's default sampling frequency: 48 kHz

# real FFT routine from NumPy
fft  = np.fft.rfft( x )
freq = np.linspace( 0, 0.5*sampling, int( 0.5*N ) + 1 ) 

# plotting the results
fig,ax = plt.subplots( 2, 1, figsize=(12,8))
ax[0].plot( t, x )
ax[0].set_xlabel( r'$t$ (ms)' )
ax[0].set_ylabel( r'Signal height in time domain (arbitrary units)' )

ax[1].plot( freq, np.abs( fft ) )
ax[1].set_xlabel( r'$\nu$ (Hz)' )
ax[1].set_ylabel( r'Signal height in frequency domain (arbitrary units)' )
ax[1].set_xlim( 0, 0.1*sampling )

plt.show()

>**Excursus: The mathematics behind the FFT**
>
>The FFT is a numerically very efficient method for the Fourier transformation of time series. Mathematically, it is based on a **discrete Fourier transform** (DFT) and utilizes the **periodicity of the complex exponential function**. The main trick of Cooley and Tukey is based on the observation that the DFT of a data set with $2n$ elements can be decomposed into two DFTs of data sets with $n$ elements. This decomposition is applied recursively until the data sets only consist of individual elements. Finally, the partial results can be reassembled into a complete Fourier transform with $2n$ elements.
>
> The discrete time series is represented as a vector $(f_0,\dots,f_{2n-1})$. The (complex) Fourier coefficients $c_m$ for $m=0, \dots, 2n-1$ of the time series are given as
>$$
c_m = \sum\limits_{k=0}^{2n-1} f_k \exp\left[-\frac{2\pi i}{2n}mk\right].
>$$
>Now the trick of Cooley and Tukey is used: the entries $f_k$ are divided into those with even and odd indices:
>$$
c_m =
\sum\limits_{k=0}^{n-1} f_{2k} \exp\left[-\frac{2\pi i}{2n}m(2k)\right] +
\sum\limits_{k=0}^{n-1} f_{2k+1} \exp\left[-\frac{2\pi i}{2n}m(2k+1)\right].
>$$
>With the definitions $f'_k \equiv f_{2k}$ and $f''_k \equiv f_{2k+1}$ and pulling the $k$-independent part out of the exponent of the exponential function, this equation can be rewritten as the sum of two Fourier coefficients $c'_m$ and $c''_m$ for the entries with even ($'$) and odd ($''$) indices:
>$$
c_m =
\sum\limits_{k=0}^{n-1} f'_{k} \exp\left[-\frac{2\pi i}{n}mk\right] +
\exp\left[-\frac{\pi i}{n}m\right]
\sum\limits_{k=0}^{n-1} f''_{k} \exp\left[-\frac{2\pi i}{n}mk\right].
>$$
>Now the cases $m<n$ and $m\geq n$ must be distinguished:
>$$
c_m = \begin{cases}
c'_m + \exp\left[-\frac{\pi i}{n}m\right] c''_m & m < n,\\
c'_{m-n} - \exp\left[-\frac{\pi i}{n}(m-n)\right] c''_{m-n} & m \geq n.\\
\end{cases}
>$$
>The speed advantage is now visible: if both $c'_m$ and $c''_m$ are calculated for all $m=0,\dots,n-1$, two Fourier coefficients of the original time series are calculated, $c_m$ and $c_{m+n}$. Except for the additional effort for the decomposition, the computational effort has thus been halved. This decomposition algorithm is now applied recursively. Ideally, for an FFT, $n$ is a power of 2, if not, further data points can simply be added by zero-padding, the algorithm is still the most efficient algorithm for Fourier transforms.

### Digital filtering
In signal processing, the term filtering is used to describe the **intentional alteration** of data using **previous knowledge** about the signal and background. A filter changes the amplitude and/or phase of a signal depending on the frequency. Classic filters, e.g., for audio signals, change the frequency response:
- A **low-pass filter** suppresses high frequencies and therefore often suppresses noise.
- A **high-pass filter** suppresses low frequencies, e.g. the 50 Hz hum of the mains voltage.
- A **bandpass filter** combines low pass and high pass filters.

Filters are used, for example, to **smooth** signals with a high noise content. The prior knowledge that is utilized here is that the signal only changes slowly within the data set, while the background noise changes more quickly. For time series, this corresponds exactly to the low-pass filter mentioned above. Classic analog dial instruments perform this smoothing "automatically" due to the inertia of the dial. In digital signal processing, there are a number of standard algorithms for smoothing signals. An easy-to-implement example of a smoothing algorithm is the **moving average**. A digital signal consisting of discrete data points $y_i$ ($i=0,\dots,N$) is filtered into a new signal $m_j$ as follows:
$$
m_j = \frac{1}{2k+1} \sum_{i = -k}^{k} y_{i+j}.
$$
The new signal $m_j$ therefore consists of the arithmetic mean over a filter width of $w=2k+1$ values - the value $y_i$ and $k$ values to the left and right of it. Caution is required at the edges of the data set: the smoothing is undefined for $j<k$ and $j>N-k$, which can be avoided by "zero padding", i.e., supplementing the data set with zero values at the edges. The parameter $k$ (or $w$) therefore determines how strongly the signal is smoothed when forming the moving average. It must be chosen small enough so as not to blur the characteristic properties of the signal and at the same time large enough to suppress the noise as strongly as possible. For time series, the choice of $k$ corresponds to the choice of the inverse cut-off frequency of the filter, i.e., large $k$ correspond to lower cut-off frequencies.

In the following code example, a time series of $N$ data points is to be filtered. It is a noisy oscillation with beat. For the moving average, $k=2$ was selected. Feel free to try it out with other values!


In [ ]:
# -------- animated_convolutionFilter.py -----------------------
# Description: example showing how a convolution filter works
#  for
#      sliding average
#      peak finder
#
# Author:      G. Quast   Nov. 2016
# dependencies: Python 3 numpy, matplotlib.pyplot 
# last modified: U. Husemann, May 2021
#---------------------------------------------------------------

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import sys, numpy as np, matplotlib.pyplot as plt
import matplotlib.animation as anim
 
# construct (rectangular) template shapes . . .
# . . . for sliding average
fwidth = 5
kwin=int(fwidth/2)
v = np.array([1. for i in range(0, 2*kwin+1)], dtype=np.float32 )
k = int(len(v)/2)

# define a signal
xmin, xmax = 0., 30.
N      = 250
xplt   = np.linspace( xmin, xmax, N )
signal = 0.5*np.sin(xplt)+0.25*np.sin(1.3*xplt)+0.25*np.sin(2.5*xplt)

# add some random (Gaussian) noise
rng = np.random.default_rng( 42 )
signal += 0.05 * rng.normal( size=N )

# define and plot initial graphics
fig = plt.figure(figsize=(10., 7.5))
ax = fig.add_subplot(1,1,1)
graph_init = ax.plot(xplt, signal, 'b-')
ax.set_ylabel('Amplitude')
ax.set_xlabel('Position')
ax.set_ylim( -1.1, 1.1 )

scale = (xmax-xmin)/N

# code relevant to parts of figure to animate
graph_signal, = ax.plot( [], [], 'g-', lw=2 )
graph_line,   = ax.plot( [], [], 'r-', lw=3 )
graph_box,    = ax.fill( [], [], color='r', alpha=0.1 )

def animate(n):
  i = n+k 
  signal[i]  = sum( v * signal[i-k:i+k+1] ) / (2*k+1)   
  graph_signal.set_data( xplt[k:i], signal[k:i] )
  graph_line.set_data( np.array( list(range(i-k, i+k+1)))*scale, v )
  graph_box.set_xy( [ [(i-k)*scale,-1], [(i+k)*scale,-1], [(i+k)*scale,1], [(i-k)*scale,1] ] )
  return graph_line, graph_signal, graph_box

ani = anim.FuncAnimation( fig, animate, frames=N-2*k, interval=30, repeat=False, blit=True )
plt.show()


Mathematically, filtering with a time-constant filter can be described as a **convolution** of the data (e.g., the time series) $y_i$ with a window function $f_i$:
$$
m_j = (f*y)_j \equiv \sum_{i = -\infty}^{+\infty} f_{i} \cdot y_{i+j}.
$$
In many cases, $f_i$ is only non-zero for a finite number of values of $i$. In electrical engineering, such filters are referred to as "finite impulse response" (FIR) filters. The **moving average** is such an FIR filter with
$$
f_i = \begin{cases}
\frac{1}{2k+1} & -k \leq i \leq k, \\
0 & \textsf{otherwise}.
\end{cases}
$$

Further examples of simple FIR filters:
- **Edge filters** for detecting edges in the signal. An edge filter has the shape of a step. The filtered signal has the greatest magnitude at points with edges, i.e., where there is a strong change in the signal between two data points:
$$
f_i = \begin{cases}
-1 & -k \leq i < 0, \\
+1 & 0 \leq i \leq k, \\
0 &\textsf{otherwise}.
\end{cases}
$$

- Filters for searching for **extreme values** of the signal (peak filter), in the form of a rectangle. The filtered signal has the greatest positive (negative) value at the maxima (minima) of the original signal:
$$
f_i = \begin{cases}
-1 & -2k \leq i < -k, \\
+1 & -k \leq i < k, \\
-1 & k \leq i \leq 2k, \\
0 &\textsf{otherwise}.
\end{cases}
$$

In image processing and automatic pattern recognition on the computer, these filters can be generalized to two-dimensional filter matrices with which, for example, photographic data can be smoothed and sharpened or the edges of objects can be detected.

### Correlation analysis
Processes such as oscillations are repeated at regular time intervals, they are **periodic**. A time series of measurements of the deflection of an oscillation therefore also repeats itself (approximately) periodically. A time series with this property is also referred to as **self-similar**. This property of self-similarity can be used, among other things, to distinguish periodic signals from non-periodic noise: The series of values of the periodic signal at different times within the time series is self-similar. However, the noise at a given point in time is often independent of the noise at all other points in time. The **autocorrelation** of a time series, i.e., the **correlation** of a time series **with itself** at two points in time $t$ and $s$, provides a quantitative measure of self-similarity. For functions of position $x$, there is an equivalent measure of self-similarity of the function with itself at different position $y$, which is called **cross-correlation**.

>**Recap: expected value, variance, covariance, correlation**
>
> The expected value (also: expectation value) of a discrete distribution of a random variable $x$ with values $x_i$ (with $i=1,\dots,n$) that have a probability $P(x_i)$ is the first moment of the distribution. It is a localization measure for the distribution and is defined as:
>$$
\mathsf{E}[x] = \sum\limits_{i=1}^n x_i P(x_i).
>$$
>For continuous random variables with a probability density $f(x)$, the expected value is defined as
>$$
\mathsf{E}[x] \equiv \int x\cdot f(x)\,\mathsf{d}x.
>$$
> The **variance** of $P(x_i)$ or $f(x)$ is defined as the second central moment of the distribution, i.e. the expected value of the squared deviation of the random variable $x$ from its expected value:
>$$
\mathsf{V}[x] \equiv \sigma^2 \equiv \mathsf{E}[(x-\mathsf{E}[x])^2]
= (\mathsf{short\,calculation}\dots)
= \mathsf{E}[x^2] - \mathsf{E}[x]^2.
>$$
> The quantity $\sigma_x=\sqrt{\sigma^2}$ is referred to as the **standard deviation** of the distribution.
>
> For two random variables $x$ and $y$, the **covariance** is defined as the expected value of the product of the deviations of $x$ and $y$ from their expected values:
>$$
\mathsf{Cov}(x,y) \equiv \sigma_{xy} \equiv \mathsf{E}\left[(x - \mathsf{E}[x])(y - \mathsf{E}[y]\right]
= (\mathsf{short\,calculation}\dots)
= \mathsf{E}[xy] - \mathsf{E}[x]\mathsf{E}[y].
>$$
> The covariance of $x$ or $y$ with itself results in the variance of these variables, e.g. $\mathsf{Cov}(x,x) = \mathsf{V}[x]$.
>
> Often more intuitive than the covariance is the Pearson's **correlation coefficient**, also known as the linear correlation coefficient:
>$$
>\rho_{xy} \equiv \frac{\mathsf{Cov}(x,y)}{\sigma_x \sigma_y}, \quad
-1 \leq \rho_{xy} \leq 1.
>$$
>In the correlation coefficient, the covariance of $x$ and $y$ is normalized to the product of the standard deviations $\sigma_x \sigma_y$, it therefore has a value range between -1 and 1:
>$$
\rho_{xy} = \begin{cases}
0 & \textsf{$x$ and $y$ (linearly) uncorrelated}, \\
+1 & \textsf{$x$ and $y$ 100\% positively (linearly) correlated},\\
-1 & \textsf{$x$ and $y$ 100\% negatively (linearly) correlated (also: anti-correlated)}.
\end{cases}
>$$

Analogous to the definition of covariance, the **autocovariance** of two members of a time series $\mathbf{y}$ at two points in time $t$ and $s$ is defined as
$$
\gamma(s,t)\equiv\mathsf{Cov}(y_t, y_s^*) \equiv
\mathsf{E}\big[ (y_t - \mathsf{E}[y_t])
(y_s - \mathsf{E}[y_s])^* \big]
= \mathsf{E}[y_t \cdot y_s^*] - \mathsf{E}[y_t] \cdot \mathsf{E}[y_s^*]
$$
(whereby this definition is also valid for complex values of $\mathbf{y}$, but in the following we will always consider real-valued time series). Analogous to the Pearson correlation coefficient, the **autocorrelation** of the members of the time series is given by the autocovariance normalized to standard deviations:
$$
\rho(s,t)\equiv\frac{\mathsf{Cov}(y_t, y_s^*)}{\sigma_t \sigma_s}.
$$
Many physical processes are **stationary**. This means, among other things, that their autocorrelation does not depend on the absolute times $t$ and $s$, but only on the **time difference** ("lag") $\tau \equiv s - t$. We also assume that $\mathsf{E}[y_t]=\mathsf{E}[y_s]=0$, i.e. all members of the time series vary around the zero point. This condition is easy to achieve for periodic processes such as oscillations by shifting the zero point of the oscillation accordingly. This results in a definition of autocorrelation that is frequently used:
$$
\rho_\tau = \frac{\gamma_\tau}{\gamma_0}
\textsf{ with } \gamma_\tau = \sum_{k=0}^{N-\tau-1} y_k^* \,y_{k+\tau}
\textsf{ and } \gamma_0 = \mathsf{V}[\mathbf{y}] = \sigma^2.
$$
Attention: $\gamma_\tau$ is referred to as an autocorrelation in NumPy even without normalization to $\gamma_0$ - please always read the documentation of the corresponding methods carefully.

#### Example: Frequency measurement with autocorrelation
In the following, the technique of autocorrelation will be used to measure the frequency of a very noisy signal. We expect the noise at a given point in time to be independent of the noise at all other points in time. This means that the noise signal is not self-similar and the autocorrelation is only different from zero for a time difference of $\tau\approx 0$. In contrast, the signal is self-similar. We therefore expect the autocorrelation of the signal to have the **same period as the signal itself**. Frequency determination with autocorrelation is used in recording studios, for example, in the audio effect "Auto-Tune", in which the pitch of human singing can be adjusted to the mathematically correct pitch in real time.

In [ ]:
"""Autocorrelation"""

import numpy as np
import matplotlib.pyplot as plt
from scipy import signal

# generate signal
nt = 500
tmin, tmax = 0, 50
times = np.linspace( tmin, tmax, nt )
signal = np.sin( times + 0.5 ) 

# add square wave noise
rng = np.random.default_rng( 42 )
noise = rng.uniform( -0.5, 0.5, nt )
signal += noise

# autocorrelation using np.correlate: mode='full' yields mirrored autocorrelation function in addition
autocorr = np.correlate( signal, signal, mode='full' )
autocorr /= autocorr[nt-1] # normalize

# autocorrelation using scalar product
gsignal, gnoise = np.zeros( nt ), np.zeros( nt )
gsignal[0] = np.inner( signal, signal )
gnoise[0] = np.inner( noise, noise )
for i in np.arange( 1, nt ):
    gsignal[i] = np.inner( signal[:-i], signal[i:] )
    gnoise[i] = np.inner( noise[:-i], noise[i:] )
acsignal = gsignal/gsignal[0]
acnoise  = gnoise/gnoise[0]

# plot results
fig,ax = plt.subplots( 2, 2, figsize=(12,8))
ax[0][0].plot( times, noise )
ax[0][0].set_xlabel( r'$t$ (arbitrary units)' )
ax[0][0].set_ylabel( r'Amplitude (arbitrary units)' )

ax[0][1].plot( times, acnoise )
ax[0][1].set_xlabel( r'$\tau$  (arbitrary units)' )
ax[0][1].set_ylabel( r'Amplitude (arbitrary units)' )

ax[1][0].plot( times, signal )
ax[1][0].set_xlabel( r'$t$  (arbitrary units)' )
ax[1][0].set_ylabel( r'Amplitude (arbitrary units)' )

ax[1][1].plot( times, acsignal )
ax[1][1].set_xlabel( r'$\tau$ ( (arbitrary units)' )
ax[1][1].set_ylabel( r'Amplitude (arbitrary units)' )

plt.show()

In Python, you can easily implement an autocorrelation yourself. As can be seen from the definition above, it consists of the scalar product of the time series $\mathbf{y}$ with a version of itself shifted by the time difference (lag) $\tau$. This is illustrated in the following animation:

In [ ]:
# script animate_autoCorrelation
''' calculation the autocorrelation function
    with animated illustration
.. author:: Guenter Quast <g.quast@kit.edu>
'''

# dependencies:  Python v3.12, numpy, matplotlib
# last modified: U. Husemann, March 2024
#--------------------------------------------------------------

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import numpy as np, matplotlib.pyplot as plt, sys
import matplotlib.animation as anim

##### ---- main program starts here -----
if __name__ == "__main__":

	print(('\n*==* script ' + sys.argv[0]+' executing'))

	# read data
	data = np.genfromtxt('data/phyphox_voice.csv', delimiter=",", skip_header=1 )

	# use only the first 250 rows of data input
	t = data[:250,0]
	y = data[:250,1]
 
	N = len(y)  
	
	# generate and plot static part of figure
	fig = plt.figure( figsize=(10.,7.5) )
	ax1 = fig.add_subplot( 2,1,1 )
	ax2 = fig.add_subplot( 2,1,2 )
	ax1.grid( True )
	ax2.grid( True )
	
	ax1.set_title( 'Autocorrelation of a periodic signal', size='xx-large' )
	ax1.set_xlabel( 'Time (ms)' )
	ax2.set_xlabel( 'Time Difference (ms)' )
	ax1.set_ylabel( 'Amplitude')
	ax2.set_ylabel( r'Autocorrelation $\rho$' )
  	
	timetxt = ax1.text(0.3, 0.9, ' ', transform=ax1.transAxes,size='large', backgroundcolor='white')
                    	
	# plot dummy versions of all objects for later animation
	graph1,  = ax1.plot( t, y, '-', color='black' )
	graph1a, = ax1.plot( [], [], '-', color='blue', lw=2 )
	graph1b, = ax1.plot( [], [], '-', color='blue', lw=2 )
	graph1c  = ax1.axvline( color='darkred')
	graph2, = ax2.plot( t, np.zeros( len(t) ), '--', color='black', lw=1 )
  	
	ax2.set_ylim(-1.,1.)
	
	# variables for dynamic part   
	nrep = N-1 # number of repetitions	
	rho    = np.zeros( N )   # vector for autocorrelations (calulated in animate)
	rho[0] = np.inner( y, y )

	def animate(n):
    	# animation loop
		global rho
		
		i = n+1
		# calculate autocorrelation at i as inner product
		rho[i] = np.inner(y[i:], y[:-i])/rho[0] 
		
		# update animation objects
		graph1a.set_data( t[i:], y[:-i] )
		graph1b.set_data( t[i:], y[i:] )
		graph1c.set_xdata( [t[i]] ) # must be a sequence type, even for a single value
		graph2, = ax2.plot(t[:i], rho[:i], '-', color='darkred', lw=2)
		timestep='i=%i' %(i)
		timetxt.set_text(timestep)
		return graph1a, graph1b, graph1c, graph2, timetxt

	# excute animation (calls animate() nrep times every 30 ms)  
	ani=anim.FuncAnimation( fig, animate, frames=nrep, interval=50, repeat=False )
       
	# write an mp4 movie using the ffmpeg encoder (to be installed separately)
	#Writer = anim.writers[ 'ffmpeg' ]
	#writer = Writer( fps=30, bitrate=64000 )
	#ani.save( "autocorr.mp4", writer=writer )
	#plt.savefig( "autocorr.pdf")
                         
	plt.show()
